**Copyright 2019 The TensorFlow Hub Authors.**

Licensed under the Apache License, Version 2.0 (the "License");

In [ ]:
# Copyright 2019 The TensorFlow Hub Authors. All Rights Reserved.
#
# Licensed under the Apache License, Version 2.0 (the "License");
# you may not use this file except in compliance with the License.
# You may obtain a copy of the License at
#
#     http://www.apache.org/licenses/LICENSE-2.0
#
# Unless required by applicable law or agreed to in writing, software
# distributed under the License is distributed on an "AS IS" BASIS,
# WITHOUT WARRANTIES OR CONDITIONS OF ANY KIND, either express or implied.
# See the License for the specific language governing permissions and
# limitations under the License.
# ==============================================================================

# 使用 Multilingual Universal Sentence Encoder 研究跨语言相似度和构建语义搜索引擎


<table class="tfo-notebook-buttons" align="left">
  <td>     <a target="_blank" href="https://tensorflow.google.cn/hub/tutorials/cross_lingual_similarity_with_tf_hub_multilingual_universal_encoder"><img src="https://tensorflow.google.cn/images/tf_logo_32px.png">在 TensorFlow.org 上查看</a> </td>
  <td><a target="_blank" href="https://colab.research.google.com/github/tensorflow/docs-l10n/blob/master/site/zh-cn/hub/tutorials/cross_lingual_similarity_with_tf_hub_multilingual_universal_encoder.ipynb"><img src="https://tensorflow.google.cn/images/colab_logo_32px.png">在 Google Colab 中运行</a></td>
  <td><a target="_blank" href="https://github.com/tensorflow/docs-l10n/blob/master/site/zh-cn/hub/tutorials/cross_lingual_similarity_with_tf_hub_multilingual_universal_encoder.ipynb"><img src="https://tensorflow.google.cn/images/GitHub-Mark-32px.png">在 GitHub 上查看源代码</a></td>
  <td><a href="https://storage.googleapis.com/tensorflow_docs/docs-l10n/site/zh-cn/hub/tutorials/cross_lingual_similarity_with_tf_hub_multilingual_universal_encoder.ipynb"><img src="https://tensorflow.google.cn/images/download_logo_32px.png">下载笔记本</a></td>
  <td>     <a href="https://tfhub.dev/google/universal-sentence-encoder-multilingual/3"><img src="https://tensorflow.google.cn/images/hub_logo_32px.png">查看 TF Hub 模型</a>   </td>
</table>

此笔记本演示了如何访问 Multilingual Universal Sentence Encoder 模块，以及如何将它用于跨多种语言的句子相似度研究。本模块是[原始 Universal Sentence Encoder 模块](https://tfhub.dev/google/universal-sentence-encoder/2)的扩展。

此笔记本分为以下两个部分：

- 第一部分展示了成对语言之间句子的可视化。这是一项学术性较强的练习。
- 在第二部分中，我们将展示如何从多种语言的 Wikipedia 语料库样本构建语义搜索引擎。

## 引用

*研究论文在使用本 Colab 中探讨的模型时应引用以下内容：*

###

[Multilingual universal sentence encoder for semantic retrieval](https://arxiv.org/abs/1907.04307)

Yinfei Yang, Daniel Cer, Amin Ahmad, Mandy Guo, Jax Law, Noah Constant, Gustavo Hernandez Abrego, Steve Yuan, Chris Tar, Yun-Hsuan Sung, Brian Strope, and Ray Kurzweil. 2019. arXiv preprint arXiv:1907.04307

## 安装

本部分将对访问 Multilingual Universal Sentence Encoder 模块的环境进行设置，并准备一组英语句子及其翻译。在以下部分中，多语模块将用于计算*跨语言*相似度。

In [ ]:
%%capture
#@title Setup Environment
# Install the latest Tensorflow version.
!pip install "tensorflow-text==2.8.*"
!pip install bokeh
!pip install simpleneighbors[annoy]
!pip install tqdm

In [ ]:
#@title Setup common imports and functions
import bokeh
import bokeh.models
import bokeh.plotting
import numpy as np
import os
import pandas as pd
import tensorflow.compat.v2 as tf
import tensorflow_hub as hub
from tensorflow_text import SentencepieceTokenizer
import sklearn.metrics.pairwise

from simpleneighbors import SimpleNeighbors
from tqdm import tqdm
from tqdm import trange

def visualize_similarity(embeddings_1, embeddings_2, labels_1, labels_2,
                         plot_title,
                         plot_width=1200, plot_height=600,
                         xaxis_font_size='12pt', yaxis_font_size='12pt'):

  assert len(embeddings_1) == len(labels_1)
  assert len(embeddings_2) == len(labels_2)

  # arccos based text similarity (Yang et al. 2019; Cer et al. 2019)
  sim = 1 - np.arccos(
      sklearn.metrics.pairwise.cosine_similarity(embeddings_1,
                                                 embeddings_2))/np.pi

  embeddings_1_col, embeddings_2_col, sim_col = [], [], []
  for i in range(len(embeddings_1)):
    for j in range(len(embeddings_2)):
      embeddings_1_col.append(labels_1[i])
      embeddings_2_col.append(labels_2[j])
      sim_col.append(sim[i][j])
  df = pd.DataFrame(zip(embeddings_1_col, embeddings_2_col, sim_col),
                    columns=['embeddings_1', 'embeddings_2', 'sim'])

  mapper = bokeh.models.LinearColorMapper(
      palette=[*reversed(bokeh.palettes.YlOrRd[9])], low=df.sim.min(),
      high=df.sim.max())

  p = bokeh.plotting.figure(title=plot_title, x_range=labels_1,
                            x_axis_location="above",
                            y_range=[*reversed(labels_2)],
                            plot_width=plot_width, plot_height=plot_height,
                            tools="save",toolbar_location='below', tooltips=[
                                ('pair', '@embeddings_1 ||| @embeddings_2'),
                                ('sim', '@sim')])
  p.rect(x="embeddings_1", y="embeddings_2", width=1, height=1, source=df,
         fill_color={'field': 'sim', 'transform': mapper}, line_color=None)

  p.title.text_font_size = '12pt'
  p.axis.axis_line_color = None
  p.axis.major_tick_line_color = None
  p.axis.major_label_standoff = 16
  p.xaxis.major_label_text_font_size = xaxis_font_size
  p.xaxis.major_label_orientation = 0.25 * np.pi
  p.yaxis.major_label_text_font_size = yaxis_font_size
  p.min_border_right = 300

  bokeh.io.output_notebook()
  bokeh.io.show(p)


下面是附加的样板代码，我们在其中导入了预训练的 ML 模型，在此笔记本中我们将用它来对文本进行编码。

In [ ]:
# The 16-language multilingual module is the default but feel free
# to pick others from the list and compare the results.
module_url = 'https://tfhub.dev/google/universal-sentence-encoder-multilingual/3' #@param ['https://tfhub.dev/google/universal-sentence-encoder-multilingual/3', 'https://tfhub.dev/google/universal-sentence-encoder-multilingual-large/3']

model = hub.load(module_url)

def embed_text(input):
  return model(input)

# 呈现语言之间的文本相似度

现在有了句子嵌入向量，我们就能呈现不同语言之间的语义相似度。

## 计算文本嵌入向量

我们首先定义一组同时翻译成各种语言的句子。然后预计算所有句子的嵌入向量。

In [ ]:
# Some texts of different lengths in different languages.
arabic_sentences = ['كلب', 'الجراء لطيفة.', 'أستمتع بالمشي لمسافات طويلة على طول الشاطئ مع كلبي.']
chinese_sentences = ['狗', '小狗很好。', '我喜欢和我的狗一起沿着海滩散步。']
english_sentences = ['dog', 'Puppies are nice.', 'I enjoy taking long walks along the beach with my dog.']
french_sentences = ['chien', 'Les chiots sont gentils.', 'J\'aime faire de longues promenades sur la plage avec mon chien.']
german_sentences = ['Hund', 'Welpen sind nett.', 'Ich genieße lange Spaziergänge am Strand entlang mit meinem Hund.']
italian_sentences = ['cane', 'I cuccioli sono carini.', 'Mi piace fare lunghe passeggiate lungo la spiaggia con il mio cane.']
japanese_sentences = ['犬', '子犬はいいです', '私は犬と一緒にビーチを散歩するのが好きです']
korean_sentences = ['개', '강아지가 좋다.', '나는 나의 개와 해변을 따라 길게 산책하는 것을 즐긴다.']
russian_sentences = ['собака', 'Милые щенки.', 'Мне нравится подолгу гулять по пляжу со своей собакой.']
spanish_sentences = ['perro', 'Los cachorros son agradables.', 'Disfruto de dar largos paseos por la playa con mi perro.']

# Multilingual example
multilingual_example = ["Willkommen zu einfachen, aber", "verrassend krachtige", "multilingüe", "compréhension du langage naturel", "модели.", "大家是什么意思" , "보다 중요한", ".اللغة التي يتحدثونها"]
multilingual_example_in_en =  ["Welcome to simple yet", "surprisingly powerful", "multilingual", "natural language understanding", "models.", "What people mean", "matters more than", "the language they speak."]


In [ ]:
# Compute embeddings.
ar_result = embed_text(arabic_sentences)
en_result = embed_text(english_sentences)
es_result = embed_text(spanish_sentences)
de_result = embed_text(german_sentences)
fr_result = embed_text(french_sentences)
it_result = embed_text(italian_sentences)
ja_result = embed_text(japanese_sentences)
ko_result = embed_text(korean_sentences)
ru_result = embed_text(russian_sentences)
zh_result = embed_text(chinese_sentences)

multilingual_result = embed_text(multilingual_example)
multilingual_in_en_result = embed_text(multilingual_example_in_en)

## 可视化相似度

有了文本嵌入向量，我们就可以利用它们的点积来呈现句子在不同语言之间的相似程度。颜色越深，嵌入向量在语义上越相似。

### 多语言相似度

In [ ]:
visualize_similarity(multilingual_in_en_result, multilingual_result,
                     multilingual_example_in_en, multilingual_example,  "Multilingual Universal Sentence Encoder for Semantic Retrieval (Yang et al., 2019)")


### 英语-阿拉伯语相似度

In [ ]:
visualize_similarity(en_result, ar_result, english_sentences, arabic_sentences, 'English-Arabic Similarity')

### 英语-俄语相似度

In [ ]:
visualize_similarity(en_result, ru_result, english_sentences, russian_sentences, 'English-Russian Similarity')

### 英语-西班牙语相似度

In [ ]:
visualize_similarity(en_result, es_result, english_sentences, spanish_sentences, 'English-Spanish Similarity')

### 英语-意大利语相似度

In [ ]:
visualize_similarity(en_result, it_result, english_sentences, italian_sentences, 'English-Italian Similarity')

### 意大利语-西班牙语相似度

In [ ]:
visualize_similarity(it_result, es_result, italian_sentences, spanish_sentences, 'Italian-Spanish Similarity')

### 英语-中文相似度

In [ ]:
visualize_similarity(en_result, zh_result, english_sentences, chinese_sentences, 'English-Chinese Similarity')

### 英语-韩语相似度

In [ ]:
visualize_similarity(en_result, ko_result, english_sentences, korean_sentences, 'English-Korean Similarity')

### 中文-韩语相似度

In [ ]:
visualize_similarity(zh_result, ko_result, chinese_sentences, korean_sentences, 'Chinese-Korean Similarity')

### 以及更多…

上面的示例可以扩展到**英语、阿拉伯语、中文、荷兰语、法语、德语、意大利语、日语、韩语、波兰语、葡萄牙语、俄语、西班牙语、泰语和土耳其语**中的任何语言对。编程愉快！

# 创建多语语义相似度搜索引擎

在前面的示例中，我们可视化了少量句子，而在本部分，我们将使用来自 Wikipedia 语料库的约 200,000 个句子构建一个语义搜索索引。其中，大约一半将使用英语，另一半使用西班牙语，以演示 Universal Sentence Encoder 的多语言功能。

## 将数据下载到索引

首先，我们将从 [News-Commentary 语料库](http://opus.nlpl.eu/News-Commentary-v11.php) [1] 中下载多种语言的新闻句子。在不失一般性的前提下，此方法应该也可以用来为其余支持的语言建立索引。

为了加快演示速度，我们将每种语言限制为 1000 个句子。

In [ ]:
corpus_metadata = [
    ('ar', 'ar-en.txt.zip', 'News-Commentary.ar-en.ar', 'Arabic'),
    ('zh', 'en-zh.txt.zip', 'News-Commentary.en-zh.zh', 'Chinese'),
    ('en', 'en-es.txt.zip', 'News-Commentary.en-es.en', 'English'),
    ('ru', 'en-ru.txt.zip', 'News-Commentary.en-ru.ru', 'Russian'),
    ('es', 'en-es.txt.zip', 'News-Commentary.en-es.es', 'Spanish'),
]

language_to_sentences = {}
language_to_news_path = {}
for language_code, zip_file, news_file, language_name in corpus_metadata:
  zip_path = tf.keras.utils.get_file(
      fname=zip_file,
      origin='http://opus.nlpl.eu/download.php?f=News-Commentary/v11/moses/' + zip_file,
      extract=True)
  news_path = os.path.join(os.path.dirname(zip_path), news_file)
  language_to_sentences[language_code] = pd.read_csv(news_path, sep='\t', header=None)[0][:1000]
  language_to_news_path[language_code] = news_path

  print('{:,} {} sentences'.format(len(language_to_sentences[language_code]), language_name))

24715264/24714354 [==============================] - 2s 0us/step
1,000 Arabic sentences
18104320/18101984 [==============================] - 2s 0us/step
1,000 Chinese sentences
28106752/28106064 [==============================] - 2s 0us/step
1,000 English sentences
24854528/24849511 [==============================] - 2s 0us/step
1,000 Russian sentences
1,000 Spanish sentences


## 使用预训练的模型将句子转换为向量

我们分*批次*计算嵌入向量，使其适合 GPU 的 RAM。

In [ ]:
# Takes about 3 minutes

batch_size = 2048
language_to_embeddings = {}
for language_code, zip_file, news_file, language_name in corpus_metadata:
  print('\nComputing {} embeddings'.format(language_name))
  with tqdm(total=len(language_to_sentences[language_code])) as pbar:
    for batch in pd.read_csv(language_to_news_path[language_code], sep='\t',header=None, chunksize=batch_size):
      language_to_embeddings.setdefault(language_code, []).extend(embed_text(batch[0]))
      pbar.update(len(batch))

  0%|          | 0/1000 [00:00<?, ?it/s]


Computing Arabic embeddings


83178it [00:30, 2768.60it/s]
  0%|          | 0/1000 [00:00<?, ?it/s]


Computing Chinese embeddings


69206it [00:18, 3664.60it/s]
  0%|          | 0/1000 [00:00<?, ?it/s]

...

238853it [00:37, 6319.00it/s]
  0%|          | 0/1000 [00:00<?, ?it/s]


Computing Russian embeddings


190092it [00:34, 5589.16it/s]
  0%|          | 0/1000 [00:00<?, ?it/s]


Computing Spanish embeddings


238819it [00:41, 5754.02it/s]


## 构建语义向量的索引

我们使用 [SimpleNeighbors](https://pypi.org/project/simpleneighbors/) 库（这是 [Annoy](https://github.com/spotify/annoy) 库的封装容器）高效地从语料库中查找结果。

In [ ]:
%%time

# Takes about 8 minutes

num_index_trees = 40
language_name_to_index = {}
embedding_dimensions = len(list(language_to_embeddings.values())[0][0])
for language_code, zip_file, news_file, language_name in corpus_metadata:
  print('\nAdding {} embeddings to index'.format(language_name))
  index = SimpleNeighbors(embedding_dimensions, metric='dot')

  for i in trange(len(language_to_sentences[language_code])):
    index.add_one(language_to_sentences[language_code][i], language_to_embeddings[language_code][i])

  print('Building {} index with {} trees...'.format(language_name, num_index_trees))
  index.build(n=num_index_trees)
  language_name_to_index[language_name] = index

  0%|          | 1/1000 [00:00<02:21,  7.04it/s]


Adding Arabic embeddings to index


  0%|          | 1/1000 [00:00<01:53,  8.84it/s]

Building Arabic index with 40 trees...

Adding Chinese embeddings to index


  0%|          | 1/1000 [00:00<01:59,  8.39it/s]

...

Building English index with 40 trees...

Adding Russian embeddings to index


  0%|          | 1/1000 [00:00<02:03,  8.06it/s]

Building Russian index with 40 trees...

Adding Spanish embeddings to index


100%|██████████| 1000/1000 [02:07<00:00,  7.84it/s]

Building Spanish index with 40 trees...
CPU times: user 11min 21s, sys: 2min 14s, total: 13min 35s
Wall time: 10min 33s


In [ ]:
%%time

# Takes about 13 minutes

num_index_trees = 60
print('Computing mixed-language index')
combined_index = SimpleNeighbors(embedding_dimensions, metric='dot')
for language_code, zip_file, news_file, language_name in corpus_metadata:
  print('Adding {} embeddings to mixed-language index'.format(language_name))
  for i in trange(len(language_to_sentences[language_code])):
    annotated_sentence = '({}) {}'.format(language_name, language_to_sentences[language_code][i])
    combined_index.add_one(annotated_sentence, language_to_embeddings[language_code][i])

print('Building mixed-language index with {} trees...'.format(num_index_trees))
combined_index.build(n=num_index_trees)

  0%|          | 1/1000 [00:00<02:00,  8.29it/s]

Computing mixed-language index
Adding Arabic embeddings to mixed-language index


  0%|          | 1/1000 [00:00<02:24,  6.89it/s]

Adding Chinese embeddings to mixed-language index


  0%|          | 1/1000 [00:00<02:05,  7.98it/s]

...

Adding Russian embeddings to mixed-language index


  0%|          | 1/1000 [00:00<02:17,  7.28it/s]

Adding Spanish embeddings to mixed-language index


100%|██████████| 1000/1000 [02:06<00:00,  7.90it/s]


Building mixed-language index with 60 trees...
CPU times: user 11min 18s, sys: 2min 13s, total: 13min 32s
Wall time: 10min 30s


## 验证语义相似度搜索引擎是否有效

我们将在本部分演示以下内容：

1. 语义搜索功能：从语料库中检索与给定查询语义相似的句子。
2. 多语言功能：查询语言和索引语言匹配时以多种语言显示
3. 跨语言功能：使用与索引语料库不同的语言发起查询
4. 混合语言语料库：以上所有内容均在一个索引中，包含来自所有语言的条目


### 语义搜索跨语言功能

在本部分中，我们将展示如何检索与一组英语例句相关的句子。待尝试的内容如下：

- 尝试一些不同的例句
- 尝试更改返回结果的数量（它们会按照相似度的顺序返回）
- 通过返回不同语言的结果来尝试跨语言功能（可以使用 [Google 翻译](http://translate.google.com)将部分结果翻译成您的母语来进行健全性检查）


In [ ]:
sample_query = 'The stock market fell four points.'  #@param ["Global warming", "Researchers made a surprising new discovery last week.", "The stock market fell four points.", "Lawmakers will vote on the proposal tomorrow."] {allow-input: true}
index_language = 'English'  #@param ["Arabic", "Chinese", "English", "French", "German", "Russian", "Spanish"]
num_results = 10  #@param {type:"slider", min:0, max:100, step:10}

query_embedding = embed_text(sample_query)[0]
search_results = language_name_to_index[index_language].nearest(query_embedding, n=num_results)

print('{} sentences similar to: "{}"\n'.format(index_language, sample_query))
search_results

English sentences similar to: "The stock market fell four points."



['Nobel laureate Amartya Sen attributed the European crisis to four failures – political, economic, social, and intellectual.',
 'Just last December, fellow economists Martin Feldstein and Nouriel Roubini each penned op-eds bravely questioning bullish market sentiment, sensibly pointing out gold’s risks.',
 'His ratings have dipped below 50% for the first time.',
 'As a result, markets were deregulated, making it easier to trade assets that were perceived to be safe, but were in fact not.',
 'Consider the advanced economies.',
 'But the agreement has three major flaws.',
 'This “predetermined equilibrium” thinking – reflected in the view that markets always self-correct – led to policy paralysis until the Great Depression, when John Maynard Keynes’s argument for government intervention to address unemployment and output gaps gained traction.',
 'Officials underestimated tail risks.',
 'Consider a couple of notorious examples.',
 'Stalin was content to settle for an empire in Eastern Eu

### 混合语料库功能

现在，我们将以英语发起查询，但结果将来自任何一种已建立索引的语言。

In [ ]:
sample_query = 'The stock market fell four points.'  #@param ["Global warming", "Researchers made a surprising new discovery last week.", "The stock market fell four points.", "Lawmakers will vote on the proposal tomorrow."] {allow-input: true}
num_results = 40  #@param {type:"slider", min:0, max:100, step:10}

query_embedding = embed_text(sample_query)[0]
search_results = language_name_to_index[index_language].nearest(query_embedding, n=num_results)

print('{} sentences similar to: "{}"\n'.format(index_language, sample_query))
search_results

English sentences similar to: "The stock market fell four points."



['Nobel laureate Amartya Sen attributed the European crisis to four failures – political, economic, social, and intellectual.',
 'It was part of the 1945 consensus.',
 'The end of the East-West ideological divide and the end of absolute faith in markets are historical turning points.',
 'Just last December, fellow economists Martin Feldstein and Nouriel Roubini each penned op-eds bravely questioning bullish market sentiment, sensibly pointing out gold’s risks.',
 'His ratings have dipped below 50% for the first time.',
 'As a result, markets were deregulated, making it easier to trade assets that were perceived to be safe, but were in fact not.',
 'Consider the advanced economies.',
 'Since their articles appeared, the price of gold has moved up still further.',
 'But the agreement has three major flaws.',
 'Gold prices even hit a record-high $1,300 recently.',
 'This “predetermined equilibrium” thinking – reflected in the view that markets always self-correct – led to policy paralysis

尝试您自己的查询：

In [ ]:
query = 'The stock market fell four points.'  #@param {type:"string"}
num_results = 30  #@param {type:"slider", min:0, max:100, step:10}

query_embedding = embed_text(sample_query)[0]
search_results = combined_index.nearest(query_embedding, n=num_results)

print('{} sentences similar to: "{}"\n'.format(index_language, query))
search_results

English sentences similar to: "The stock market fell four points."



['(Chinese) 新兴市场的号角',
 '(English) It was part of the 1945 consensus.',
 '(Russian) Брюссель. Цунами, пронёсшееся по финансовым рынкам, является глобальной катастрофой.',
 '(Arabic) هناك أربعة شروط مسبقة لتحقيق النجاح الأوروبي في أفغانستان:',
 '(Spanish) Su índice de popularidad ha caído por primera vez por debajo del 50 por ciento.',
 '(English) His ratings have dipped below 50% for the first time.',
 '(Russian) Впервые его рейтинг опустился ниже 50%.',
 '(English) As a result, markets were deregulated, making it easier to trade assets that were perceived to be safe, but were in fact not.',
 '(Arabic) وكانت التطورات التي شهدتها سوق العمل أكثر تشجيعا، فهي على النقيض من أسواق الأصول تعكس النتائج وليس التوقعات. وهنا أيضاً كانت الأخبار طيبة. فقد أصبحت سوق العمل أكثر إحكاما، حيث ظلت البطالة عند مستوى 3.5% وكانت نسبة الوظائف إلى الطلبات المقدمة فوق مستوى التعادل.',
 '(Russian) Это было частью консенсуса 1945 года.',
 '(English) Consider the advanced economies.',
 '(English) Since their artic

# 其他主题

## 多语言

最后，我们建议您尝试使用任何一种支持的语言进行查询：**英语、阿拉伯语、中文、荷兰语、法语、德语、意大利语、日语、韩语、波兰语、葡萄牙语、俄语、西班牙语、泰语和土耳其语**。

另外，即使我们仅对部分语言建立了索引，您也可以使用任何支持的语言为内容建立索引。

## 模型变体

我们提供已针对各个方面（如内存、延迟和/或质量）进行了优化的 Universal Sentence Encoder 模型变体。您可以随意试验，找出最合适的一个。

## 最近邻库

我们使用 Annoy 来高效查找最近邻。请参阅[权衡部分](https://github.com/spotify/annoy/blob/master/README.rst#tradeoffs)，以了解要搜索的树的数量（取决于内存）和项目的数量（取决于延迟）。SimpleNeighbors 仅允许控制树的数量，但对代码进行重构以直接使用 Annoy 应该会比较简单，我们只想为普通用户尽可能简化此代码。

如果 Annoy 不适合您的应用，请试试 [FAISS](https://github.com/facebookresearch/faiss)。

*祝您顺利构建多语言语义应用！*

[1] J. Tiedemann, 2012, [Parallel Data, Tools and Interfaces in OPUS](http://www.lrec-conf.org/proceedings/lrec2012/pdf/463_Paper.pdf). 第八届语言资源与评估国际会议论文集 (LREC 2012)